In [21]:
import matplotlib.pyplot as plt
plt.rcParams["font.size"] = 16

# 1.A : Model

Canva

# 1.B : Jumps (Ryu (data + fitted) + 3 trajectories (Ryu + mu2 + theta2))

In [22]:
import matplotlib.pyplot as plt
import numpy as np
from scipy.optimize import curve_fit
from scipy.stats import gamma
plt.rcParams["font.size"] = 16


def proba_gamma(mu: float, theta: float, L: float) -> float:
    alpha_gamma = mu**2 / theta**2
    beta_gamma = theta**2 / mu
    return gamma.pdf(L, a=alpha_gamma, scale=beta_gamma)


# Données expérimentales
x = np.arange(0, 150, 10)
y = np.array([10, 140, 240, 200, 130, 125, 90, 60, 30, 25, 20, 10, 15, 7, 5], dtype=float)
y /= np.sum(y)  # normalisation à 1

# PDF théorique
x_fine = np.arange(0, 150, 1)

# Fit
popt, pcov = curve_fit(
    lambda x, mu, theta: proba_gamma(mu, theta, x) * 10,
    x,
    y,
    p0=[30, 15],
    bounds=(0, np.inf),
    maxfev=10000
)

mu, theta = popt

# PDF continue
p = proba_gamma(mu, theta, x_fine)

# Normalisation correcte
p /= np.sum(p)

# Passage en probabilité par bin
bin_width = 10
p_plot = p * bin_width

# Plot
plt.figure(figsize=(8,6), dpi=1200)

plt.bar(x, y, width=8, edgecolor="black",
        color="red", alpha=0.5, label="Data from Ryu et al. 2022\nExtracted from Figure 3.B")

plt.plot(x_fine, p_plot, lw=2, color="red",
         label=f"Gamma fit : (μ,θ) = ({mu:.0f},{theta:.0f})nm")

plt.xlabel("Step size (nm)")
plt.ylabel("Probability")
plt.grid(alpha=0.3)
plt.legend()
plt.tight_layout()
plt.show()


# 1.C : Properties of the Gamma distrib

In [23]:
import matplotlib.pyplot as plt
import numpy as np
from nucleo.simulation.probabilities import proba_gamma

plt.rcParams["font.size"] = 16

x_fine = np.arange(0, 500, 1)
params = [
    (100, 20),
    (200, 20),
    (200, 200),
]

cmap = plt.cm.Reds
colors = [cmap(0.4), cmap(0.65), cmap(0.9)]

plt.figure(figsize=(8,6), dpi=1200)

for (mu, theta), color in zip(params, colors):
    p = proba_gamma(mu=mu, theta=theta, L=x_fine)
    
    plt.plot(
        x_fine,
        p,
        lw=2.5,
        color=color,
        label=f"(μ,θ) = ({mu},{theta})"
    )

plt.xlabel(r"Step size $(\sigma)$")
plt.ylabel("Probability density")
plt.grid(True, alpha=0.3)
plt.legend(loc="upper right", ncols=1)
plt.tight_layout()
plt.show()

# 1.D : Chromatin lanscapes (homogeneous + periodic + random)

In [24]:
from nucleo.simulation.chromatin import alpha_random, alpha_periodic, alpha_homogeneous
import numpy as np
from matplotlib import pyplot as plt
plt.rcParams["font.size"] = 16

# Values in nm
s = 150
l = 10
alphao = 0
alphaf = 1
Lmin = 0
Lmax = 500
bps = 1

# Landscapes
obs_1 = alpha_homogeneous(s=s, l=l, alphao=alphao, alphaf=alphaf, Lmin=0, Lmax=Lmax, bps=bps)
obs_2 = alpha_periodic(s=s, l=l, alphao=alphao, alphaf=alphaf, Lmin=0, Lmax=Lmax, bps=bps)
obs_3 = alpha_random(s=s, l=l, alphao=alphao, alphaf=alphaf, Lmin=0, Lmax=Lmax, bps=bps)
x = np.arange(0, len(obs_1), 1)

# -------------------------------
# Homogeneous
# -------------------------------
plt.figure(figsize=(8,5), dpi=1200)

plt.plot(x, obs_1, c="b", lw=3)
plt.title("Homogeneous")
plt.xlabel("x")
plt.ylabel(r"Accessibility $\alpha$")
plt.ylim([-0.1, 1.1])
plt.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()


# -------------------------------
# Periodic
# -------------------------------
plt.figure(figsize=(8,5), dpi=1200)

plt.step(x, obs_2, c="b", lw=3)
plt.title("Periodic")
plt.xlabel("x")
# plt.ylabel(r"Accessibility $\alpha$")
plt.ylim([-0.1, 1.1])
plt.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()


# -------------------------------
# Random
# -------------------------------
plt.figure(figsize=(8,5), dpi=1200)

plt.step(x, obs_3, c="b", lw=3)
plt.title("Random")
plt.xlabel("x")
# plt.ylabel(r"Accessibility $\alpha$")
plt.ylim([-0.1, 1.1])
plt.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()


# 1.E : Linker and RoadBlocks distribution

In [25]:
# Librairies
import numpy as np
import matplotlib.pyplot as plt
import polars as pl
from polars import selectors as cs
from pathlib import Path
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from nucleo.metrics.utils import listoflist_into_matrix
plt.rcParams["font.size"] = 16

# Data
root = Path("/home/nicolas/Documents/Workspace/nucleo/outputs/FIG1/FIG1E/nucleo__fig1_0")
paths = [str(p) for p in root.rglob("*.parquet")]
df_sorted = (
    pl.scan_parquet(paths)
    .select(
        cs.string() | cs.boolean() |  cs.integer() |  cs.float() | 
        pl.col("s_points") | pl.col("s_distrib") | pl.col("l_points") | pl.col("l_distrib")
      )
    .collect()
    .sort(by=["landscape", "bpmin", "l"],
          descending=[False, False, False]
        )
)

obs_points_data = df_sorted["s_points"].to_list()
obs_points_data = listoflist_into_matrix(obs_points_data)
obs_points = np.nanmean(obs_points_data,axis=0)

obs_distrib_data = df_sorted["s_distrib"].to_list()
obs_distrib_data = listoflist_into_matrix(obs_distrib_data)
obs_distrib = np.nanmean(obs_distrib_data,axis=0)

link_points_data = df_sorted["l_points"].to_list()
link_points_data = listoflist_into_matrix(link_points_data)
link_points = np.nanmean(link_points_data,axis=0)

link_distrib_data = df_sorted["l_distrib"].to_list()
link_distrib_data = listoflist_into_matrix(link_distrib_data)
link_distrib = np.nanmean(link_distrib_data,axis=0)


# Theory
from scipy.special import factorial

def th_linkers(l, lmoy):
    A = lmoy * (1 - np.exp(-1 / lmoy))
    P = A * (np.exp(1 / lmoy) - 1) * np.exp(-l / lmoy)
    return P / np.sum(P)


def th_roadblocks(m, lmoy):
    m = np.atleast_1d(m).astype(int)
    A = np.exp(1 / lmoy) - 1
    P = np.array([1 / (lmoy**mi * A * factorial(mi)) for mi in m], dtype=float)
    return P / np.sum(P)


# Plot
fig, axes = plt.subplots(ncols=1 , nrows=2, figsize=(8,6), dpi=1200)

s = 150
lmoy = 10

theory_distrib = th_linkers(link_points, lmoy)

axes[0].plot(link_points, link_distrib, label='Simulations',
             color='lightblue', alpha=1, marker='o', lw=2)
axes[0].plot(link_points, theory_distrib, label="Theory",
             color='black', ls="--", lw=2)

axes[0].set_xlabel('Size of linkers')
axes[0].set_ylabel('Distribution')
axes[0].set_ylim([-0.10, 1.10])
axes[0].grid(True, alpha=0.3)
axes[0].legend(loc="upper right")

axins = inset_axes(axes[0],
                   width="30%", 
                   height="50%",
                   loc='upper center')

axins.plot(link_points, link_distrib,
           color='lightblue', marker='o', lw=2)
axins.plot(link_points, theory_distrib,
           color='black', ls="--", lw=2)
axins.tick_params(axis='both',
                  which='both',
                  direction='in')

axins.set_xlim(0, 20)

mask_zoom = (link_points >= 0) & (link_points <= 20)
y_min = min(link_distrib[mask_zoom].min(),
            theory_distrib[mask_zoom].min())
y_max = max(link_distrib[mask_zoom].max(),
            theory_distrib[mask_zoom].max())

axins.set_ylim(y_min*0.9, y_max*1.1)

axins.grid(True, alpha=0.2)

mask_s = (obs_distrib != 0)
obs_points = obs_points[mask_s]
obs_distrib = obs_distrib[mask_s]

theory_distrib = th_roadblocks(obs_points//s, lmoy)

axes[1].plot(obs_points//s, obs_distrib, label='Simulations',
      color='darkslategray', alpha=1, marker='o', lw=2)
axes[1].plot(obs_points//s, theory_distrib, label="Theory",
             color='black', ls="--", lw=2)

axes[1].set_xticks(np.arange(1, 6, 1, dtype=int))
axes[1].set_ylim([-0.10, 1.10])
axes[1].set_xlabel("Consecutive roadblocks")
axes[1].set_ylabel('Distribution')
axes[1].grid(True, alpha=0.3)
axes[1].legend(loc="upper right")

plt.tight_layout()
plt.show()

/tmp/ipykernel_26637/1849075418.py:121: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  plt.tight_layout()


# .